<div style=" background-color: RGB(0,114,200);" >
<h1 style="margin: auto; padding: 7px 0; color:#fff; text-align: center">PROJET 5</h1>
<h2 style="margin: auto; padding: 15px 0; color:#fff; text-align: center">BottleNeck - Optimiser la gestion des données d'une boutique
</h2>
</div>

In [9]:
import pandas as pd
import numpy as np
from ydata_profiling import ProfileReport
import datetime

In [10]:
erp = pd.read_csv("../Source/Fichier_erp.csv", delimiter=";")
web = pd.read_csv("../Source/Fichier_web.csv", delimiter=";")
liaison = pd.read_csv("../Source/Fichier_liaison.csv", delimiter=";")

<div style="background-color: RGB(0,150,250);" >
<h2 style="margin: auto; padding: 20px; color:#fff; ">Etape 1 - Exploration du fichier ERP (Référence produit)</h2>
</div>

In [11]:
profileERP = ProfileReport(erp, title="Profiling Report ERG")
profileERP

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [12]:

#Points de vérification ERG:
#//DONE:    #Enlever les données qui ne concerne pas les produits en ligne 
#//DONE:    #Dtypes de price en float + vérif de caractères inhabituelles dans la colonne et traitement de ceux-ci 
#//DONE:    #Gerer les stock négatifs 
#//DONE:    #prix négatifs (sera regler lors de la vérif de caractère) 
#//DONE:    #vérifier s'il y a des statuts de stock mal resneigné pour la quantité de stock (instock mais stock < 0) 
#//DONE:    #Vérifier le dataType de chacunes des colonnes 

In [13]:
#On affiche les valeurs abbérentes trouvé
neg_price_stock = erp.loc[(erp['price'] <= "0") | (erp['stock_quantity'] < 0)]
neg_price_stock

product_id  onsale_web price  stock_quantity stock_status
449        4973           0    10              -1   outofstock
469        5017           0    -8               0   outofstock
573        5700           1  44,5              -1   outofstock
739        6594           0    -1             192      instock

In [14]:
#création d'une fonction pour remplacer les "," et "-" en "." de la colonne price

def cleaned_price(valeurs):
    cleaned_values = valeurs.replace(',','.').replace('-', '')
    return float(cleaned_values)

erp['price'] = erp['price'].apply(cleaned_price)


In [15]:
#Enlever les - devant les stocks car des stocks ne peutx pas être négatif
erp["stock_quantity"] = erp['stock_quantity'].abs()

In [16]:
#On vérifie que les stocks ont bine été traité
erp.loc[(erp["product_id"] == 4973) | (erp["product_id"] == 5700)]

product_id  onsale_web  price  stock_quantity stock_status
449        4973           0   10.0               1   outofstock
573        5700           1   44.5               1   outofstock

In [17]:
#on enleve les données non référencé en ligne
erp = erp.loc[erp['onsale_web'] == 1]
erp = erp.reset_index(drop=True)
erp

product_id  onsale_web  price  stock_quantity stock_status
0          3847           1   24.2               0   outofstock
1          3849           1   34.3               0   outofstock
2          3850           1   20.8               0   outofstock
3          4032           1   14.1               0   outofstock
4          4039           1   46.0               0   outofstock
..          ...         ...    ...             ...          ...
712        6930           1    8.4              83      instock
713        7023           1   27.5              15      instock
714        7025           1   69.0               2      instock
715        7247           1   54.8              23      instock
716        7338           1   16.3              45      instock

[717 rows x 5 columns]

In [18]:
# On vérifie s'il y a des statuts de stock mal renseigné pour la quantité de stock (outofstock mais stock > 0)
erp.loc[(erp["stock_quantity"] != 0) & (erp["stock_status"] == "outofstock")]

product_id  onsale_web  price  stock_quantity stock_status
531        5700           1   44.5               1   outofstock
585        5826           1   41.2              12   outofstock

In [19]:
erp.loc[(erp["stock_quantity"] != 0) & (erp["stock_status"] == "outofstock"), 'stock_status'] = 'instock'

In [20]:
erp.loc[(erp["product_id"] == 5700) | (erp["product_id"] == 5826)]


product_id  onsale_web  price  stock_quantity stock_status
531        5700           1   44.5               1      instock
585        5826           1   41.2              12      instock

In [21]:
erp.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 717 entries, 0 to 716
Data columns (total 5 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   product_id      717 non-null    int64  
 1   onsale_web      717 non-null    int64  
 2   price           717 non-null    float64
 3   stock_quantity  717 non-null    int64  
 4   stock_status    717 non-null    object 
dtypes: float64(1), int64(3), object(1)
memory usage: 28.1+ KB


In [22]:
profileERP = ProfileReport(erp, title="Profiling Report ERG")
profileERP

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [23]:
erp.loc[(erp['product_id'] == 4594) | (erp['product_id'] == 5070) |(erp['product_id'] == 5075)]

product_id  onsale_web  price  stock_quantity stock_status
228        4594           1  144.0               0   outofstock
449        5070           1   84.7               0   outofstock
450        5075           1   43.3               0   outofstock

<div style="background-color: RGB(0,150,250);" >
<h2 style="margin: auto; padding: 20px; color:#fff; ">Etape 2 - Exploration du fichier Web (Produits commercialisés en ligne)</h2>
</div>

In [24]:
web

sku  virtual  downloadable  rating_count  average_rating  total_sales  \
0     16004        0             0             0             0.0          5.0   
1       NaN        0             0             0             NaN          NaN   
2     15075        0             0             0             0.0          3.0   
3     16209        0             0             0             0.0          6.0   
4     15763        0             0             0             0.0          1.0   
...     ...      ...           ...           ...             ...          ...   
1508  12881        0             0             0             0.0          2.0   
1509  15663        0             0             0             0.0          3.0   
1510  15910        0             0             0             0.0          0.0   
1511     38        0             0             0             0.0         38.0   
1512  13599        0             0             0             0.0          1.0   

     tax_status  tax_class  post_author            post_date  ...  \
0           NaN        NaN          2.0  2018-06-07 16:27:25  ...   
1           NaN        NaN          NaN                  NaN  ...   
2       taxable        NaN          2.0  2018-02-14 15:39:43  ...   
3       taxable        NaN          2.0  2018-02-14 17:15:31  ...   
4           NaN        NaN          2.0  2020-01-25 14:08:16  ...   
...         ...        ...          ...                  ...  ...   
1508        NaN        NaN          2.0  2019-03-28 15:25:14  ...   
1509    taxable        NaN          2.0  2018-02-27 10:27:01  ...   
1510    taxable        NaN          2.0  2019-03-28 10:59:43  ...   
1511        NaN        NaN          2.0  2018-04-18 12:25:58  ...   
1512        NaN        NaN          2.0  2018-03-01 14:12:39  ...   

                                              post_name        post_modified  \
0                       chateau-du-couvent-pomerol-2017  2020-08-25 18:35:02   
1                                                   NaN                  NaN   
2                     pares-balta-penedes-indigena-2017  2020-08-20 15:35:02   
3                        maurel-cabardes-tradition-2017  2020-08-05 18:05:03   
4     domaine-de-la-monardiere-vacqueyras-les-vieill...  2020-08-21 11:35:02   
...                                                 ...                  ...   
1508                 montbourgeau-etoile-vin-jaune-2009  2019-12-30 10:30:01   
1509  chermette-domaine-du-vissoux-brouilly-pierreux...  2020-08-01 09:35:02   
1510     thevenet-quintaine-vire-clesse-la-bongran-2015  2020-08-14 10:45:02   
1511         emile-boeckel-cremant-brut-blanc-de-blancs  2020-08-27 17:15:03   
1512     champagne-mailly-grand-cru-blanc-de-pinot-noir  2020-08-26 18:05:02   

        post_modified_gmt post_content_filtered post_parent  \
0     2020-08-25 16:35:02                   NaN         0.0   
1                     NaN                   NaN         NaN   
2     2020-08-20 13:35:02                   NaN         0.0   
3     2020-08-05 16:05:03                   NaN         0.0   
4     2020-08-21 09:35:02                   NaN         0.0   
...                   ...                   ...         ...   
1508  2019-12-30 09:30:01                   NaN         0.0   
1509  2020-08-01 07:35:02                   NaN         0.0   
1510  2020-08-14 08:45:02                   NaN         0.0   
1511  2020-08-27 15:15:03                   NaN         0.0   
1512  2020-08-26 16:05:02                   NaN         0.0   

                                                   guid menu_order  \
0     https://www.bottle-neck.fr/wp-content/uploads/...        0.0   
1                                                   NaN        NaN   
2     https://www.bottle-neck.fr/?post_type=product&...        0.0   
3     https://www.bottle-neck.fr/?post_type=product&...        0.0   
4     https://www.bottle-neck.fr/wp-content/uploads/...        0.0   
...                                                 ...        ...  

In [25]:
profileWEB = ProfileReport(web, title="Profiling Report WEB")
profileWEB

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [26]:
'''
Points de vérification WEB:
//DONE:- Enlever les lignes qui corresponde à une image du produit 
//DONE- Enlever les lignes et colonnes totalement vides 

//FIXME:- 'sku' : format text (convertir en INT) + Valeurs manquantes + valeurs 13127 et 13127-1 à vérifier + 
//DONE:- 'virtual' : supprimer la colonne
//DONE:- 'downloadable' : supprimer la colonne
//DONE- 'rating_count' : supprimer la colonne
//DONE- 'average_rating' supprimer la colonne
//FIXME- 'total_sales' : Convertir en integer + valeur identique à sku '38'
//DONE- 'tax_status' : supprimer la colonne
//DONE- 'tax_class' : supprimer la colonne
//DONE- 'post_author' : Convertir en integer
//DONE- 'post_date' : Convertir en datetime
//DONE- 'post_date_gmt' : Convertir en datetime
//DONE- 'post_content' : supprimer la colonne
//FIXME- 'post_title' : certains titres sont au format HTML mais ce n'est pas très utile + certains produits se repètent (j'en fais quoi ?)
//DONE- 'post_excerpt' supprimer la colonne
//DONE- 'post_status' : supprimer la colonne
//DONE- 'comment_status' : supprimer la colonne
//DONE- 'ping_status' : supprimer la colonne
//DONE- 'post_password' : supprimer la colonne
//DONE- 'post_name' : supprimer la colonne
//DONE- 'post_modified' : Convertir en datetime
//DONE- 'post_modified_gmt' : Convertir en datetime
//DONE- 'post_content_filtered' : supprimer la colonne
//DONE- 'post_parent' : supprimer la colonne
//DONE- 'guid' : les liens marche pas mais bon on va dire que c'est bon
//DONE- 'menu_order' : supprimer la colonne
//FIXME- 'post_type' : Trouver la ligne qui apparait en double sur le post_type
//DONE- 'post_mime_type' : supprimer la colonne
//DONE- 'comment_count' : supprimer la colonne
'''

"\nPoints de vérification WEB:\n//DONE:- Enlever les lignes qui corresponde à une image du produit \n//DONE- Enlever les lignes et colonnes totalement vides \n\n//FIXME:- 'sku' : format text (convertir en INT) + Valeurs manquantes + valeurs 13127 et 13127-1 à vérifier + \n//DONE:- 'virtual' : supprimer la colonne\n//DONE:- 'downloadable' : supprimer la colonne\n//DONE- 'rating_count' : supprimer la colonne\n//DONE- 'average_rating' supprimer la colonne\n//FIXME- 'total_sales' : Convertir en integer + valeur identique à sku '38'\n//DONE- 'tax_status' : supprimer la colonne\n//DONE- 'tax_class' : supprimer la colonne\n//DONE- 'post_author' : Convertir en integer\n//DONE- 'post_date' : Convertir en datetime\n//DONE- 'post_date_gmt' : Convertir en datetime\n//DONE- 'post_content' : supprimer la colonne\n//FIXME- 'post_title' : certains titres sont au format HTML mais ce n'est pas très utile + certains produits se repètent (j'en fais quoi ?)\n//DONE- 'post_excerpt' supprimer la colonne\n//D

In [27]:
#Enlever les lignes et colonnes totalement vides
print(web.shape)
web = web.dropna(thresh=19)
web = web.reset_index(drop=True)
print(web.shape)


(1513, 28)
(1430, 28)


In [28]:
#Garder les lignes qui corresponde au produit 
web = web.loc[web['post_type'] == 'product']
web = web.reset_index(drop=True)
web

sku  virtual  downloadable  rating_count  average_rating  total_sales  \
0    15075        0             0             0             0.0          3.0   
1    16209        0             0             0             0.0          6.0   
2    13895        0             0             0             0.0          0.0   
3    12857        0             0             0             0.0          0.0   
4    14106        0             0             0             0.0          0.0   
..     ...      ...           ...           ...             ...          ...   
711  15941        0             0             0             0.0          4.0   
712  10459        0             0             0             0.0          0.0   
713  16320        0             0             0             0.0          3.0   
714  15663        0             0             0             0.0          3.0   
715  15910        0             0             0             0.0          0.0   

    tax_status  tax_class  post_author            post_date  ...  \
0      taxable        NaN          2.0  2018-02-14 15:39:43  ...   
1      taxable        NaN          2.0  2018-02-14 17:15:31  ...   
2      taxable        NaN          2.0  2019-03-19 10:41:50  ...   
3      taxable        NaN          2.0  2018-04-12 17:56:13  ...   
4      taxable        NaN          2.0  2019-06-08 09:54:21  ...   
..         ...        ...          ...                  ...  ...   
711    taxable        NaN          2.0  2018-02-12 14:26:52  ...   
712    taxable        NaN          2.0  2018-04-13 15:58:19  ...   
713    taxable        NaN          2.0  2018-02-12 12:49:29  ...   
714    taxable        NaN          2.0  2018-02-27 10:27:01  ...   
715    taxable        NaN          2.0  2019-03-28 10:59:43  ...   

                                             post_name        post_modified  \
0                    pares-balta-penedes-indigena-2017  2020-08-20 15:35:02   
1                       maurel-cabardes-tradition-2017  2020-08-05 18:05:03   
2           chateau-saransot-dupre-bordeaux-blanc-2016  2020-04-25 21:11:40   
3    chateau-de-puligny-montrachet-1cru-champ-canet...  2020-02-06 16:35:02   
4                  stephane-tissot-chateau-chalon-2011  2020-05-29 17:35:03   
..                                                 ...                  ...   
711                         jerome-cotes-du-rhone-2018  2020-06-25 14:00:03   
712  alphonse-mellot-sancerre-rouge-generation-xix-...  2020-08-24 14:05:02   
713  mourgues-du-gres-costieres-de-nimes-terre-darg...  2020-08-25 11:15:03   
714  chermette-domaine-du-vissoux-brouilly-pierreux...  2020-08-01 09:35:02   
715     thevenet-quintaine-vire-clesse-la-bongran-2015  2020-08-14 10:45:02   

       post_modified_gmt post_content_filtered post_parent  \
0    2020-08-20 13:35:02                   NaN         0.0   
1    2020-08-05 16:05:03                   NaN         0.0   
2    2020-04-25 19:11:40                   NaN         0.0   
3    2020-02-06 15:35:02                   NaN         0.0   
4    2020-05-29 15:35:03                   NaN         0.0   
..                   ...                   ...         ...   
711  2020-06-25 12:00:03                   NaN         0.0   
712  2020-08-24 12:05:02                   NaN         0.0   
713  2020-08-25 09:15:03                   NaN         0.0   
714  2020-08-01 07:35:02                   NaN         0.0   
715  2020-08-14 08:45:02                   NaN         0.0   

                                                  guid menu_order  post_type  \
0    https://www.bottle-neck.fr/?post_type=product&...        0.0    product   
1    https://www.bottle-neck.fr/?post_type=product&...        0.0    product   
2    https://www.bottle-neck.fr/?post_type=product&...        0.0    product   
3    https://www.bottle-neck.fr/?post_type=product&...        0.0    product   
4    https://www.bottle-neck.fr/?post_type=product&...        0.0    product   
..                                                 ... 

In [29]:
#supprimer les colonne null et remplissage des valeurs NaN en 0
col = ['virtual','downloadable', 'tax_status','rating_count', 'average_rating', 'tax_class', 'post_excerpt','post_content','post_name','guid', 'post_password','post_content_filtered', 'post_parent', 'menu_order', 'post_mime_type', 'comment_count', 'post_status','comment_status', 'ping_status' ]

web.drop(columns=col, inplace=True)
web.fillna(0)

sku  total_sales  post_author            post_date  \
0    15075          3.0          2.0  2018-02-14 15:39:43   
1    16209          6.0          2.0  2018-02-14 17:15:31   
2    13895          0.0          2.0  2019-03-19 10:41:50   
3    12857          0.0          2.0  2018-04-12 17:56:13   
4    14106          0.0          2.0  2019-06-08 09:54:21   
..     ...          ...          ...                  ...   
711  15941          4.0          2.0  2018-02-12 14:26:52   
712  10459          0.0          2.0  2018-04-13 15:58:19   
713  16320          3.0          2.0  2018-02-12 12:49:29   
714  15663          3.0          2.0  2018-02-27 10:27:01   
715  15910          0.0          2.0  2019-03-28 10:59:43   

           post_date_gmt                                         post_title  \
0    2018-02-14 14:39:43                  Parés Baltà Penedès Indigena 2017   
1    2018-02-14 16:15:31                     Maurel Cabardès Tradition 2017   
2    2019-03-19 09:41:50         Château Saransot-Dupré Bordeaux Blanc 2016   
3    2018-04-12 15:56:13  Château de Meursault Puligny-Montrachet 1er Cr...   
4    2019-06-08 07:54:21                Stéphane Tissot Château-Chalon 2011   
..                   ...                                                ...   
711  2018-02-12 13:26:52    Domaine de la Jérôme Côtes du Rhône Village 201   
712  2018-04-13 13:58:19  Alphonse Mellot Sancerre Rouge Génération XIX ...   
713  2018-02-12 11:49:29  Mourgues du Grès IGP Pont du Gard Terre d'Arge...   
714  2018-02-27 09:27:01  Chermette Domaine du Vissoux Brouilly Pierreux...   
715  2019-03-28 09:59:43     Thevenet Quintaine Viré-Clessé La Bongran 2015   

           post_modified    post_modified_gmt post_type  
0    2020-08-20 15:35:02  2020-08-20 13:35:02   product  
1    2020-08-05 18:05:03  2020-08-05 16:05:03   product  
2    2020-04-25 21:11:40  2020-04-25 19:11:40   product  
3    2020-02-06 16:35:02  2020-02-06 15:35:02   product  
4    2020-05-29 17:35:03  2020-05-29 15:35:03   product  
..                   ...                  ...       ...  
711  2020-06-25 14:00:03  2020-06-25 12:00:03   product  
712  2020-08-24 14:05:02  2020-08-24 12:05:02   product  
713  2020-08-25 11:15:03  2020-08-25 09:15:03   product  
714  2020-08-01 09:35:02  2020-08-01 07:35:02   product  
715  2020-08-14 10:45:02  2020-08-14 08:45:02   product  

[716 rows x 9 columns]

In [30]:
#conversion en datetime des dates et post_author+total_sales en integer
web['post_date'] = pd.to_datetime(web['post_date'])
web['post_date_gmt'] = pd.to_datetime(web['post_date_gmt'])
web['post_modified'] = pd.to_datetime(web['post_modified'])
web['post_modified_gmt'] = pd.to_datetime(web['post_modified_gmt'])
web['total_sales'] = web['total_sales'].astype(int)
web['post_author'] = web['post_author'].astype(int)
web.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 716 entries, 0 to 715
Data columns (total 9 columns):
 #   Column             Non-Null Count  Dtype         
---  ------             --------------  -----         
 0   sku                714 non-null    object        
 1   total_sales        716 non-null    int64         
 2   post_author        716 non-null    int64         
 3   post_date          716 non-null    datetime64[ns]
 4   post_date_gmt      716 non-null    datetime64[ns]
 5   post_title         716 non-null    object        
 6   post_modified      716 non-null    datetime64[ns]
 7   post_modified_gmt  716 non-null    datetime64[ns]
 8   post_type          716 non-null    object        
dtypes: datetime64[ns](4), int64(2), object(3)
memory usage: 50.5+ KB


In [31]:
web.head()

sku  total_sales  post_author           post_date       post_date_gmt  \
0  15075            3            2 2018-02-14 15:39:43 2018-02-14 14:39:43   
1  16209            6            2 2018-02-14 17:15:31 2018-02-14 16:15:31   
2  13895            0            2 2019-03-19 10:41:50 2019-03-19 09:41:50   
3  12857            0            2 2018-04-12 17:56:13 2018-04-12 15:56:13   
4  14106            0            2 2019-06-08 09:54:21 2019-06-08 07:54:21   

                                          post_title       post_modified  \
0                  Parés Baltà Penedès Indigena 2017 2020-08-20 15:35:02   
1                     Maurel Cabardès Tradition 2017 2020-08-05 18:05:03   
2         Château Saransot-Dupré Bordeaux Blanc 2016 2020-04-25 21:11:40   
3  Château de Meursault Puligny-Montrachet 1er Cr... 2020-02-06 16:35:02   
4                Stéphane Tissot Château-Chalon 2011 2020-05-29 17:35:03   

    post_modified_gmt post_type  
0 2020-08-20 13:35:02   product  
1 2020-08-05 16:05:03   product  
2 2020-04-25 19:11:40   product  
3 2020-02-06 15:35:02   product  
4 2020-05-29 15:35:03   product

<div style="background-color: RGB(400,150,50);" >
<h2 style="margin: auto; padding: 20px; color:#fff; ">ZONE DE TEST </h2>
</div>

In [32]:
web.loc[web['post_title'].duplicated()]


sku  total_sales  post_author           post_date       post_date_gmt  \
316  14828            0            2 2018-11-26 09:52:56 2018-11-26 08:52:56   
462  16034            3            2 2018-09-25 15:35:26 2018-09-25 13:35:26   
654  16068            1            2 2020-02-22 14:28:32 2020-02-22 13:28:32   

                                            post_title       post_modified  \
316  Marc Colin Et Fils Chassagne-Montrachet Blanc ... 2020-03-27 09:30:10   
462       Clos du Mont-Olivet Châteauneuf-du-Pape 2007 2020-08-21 14:25:03   
654           Domaine Hauvette IGP Alpilles Jaspe 2017 2020-08-26 16:05:02   

      post_modified_gmt post_type  
316 2020-03-27 08:30:10   product  
462 2020-08-21 12:25:03   product  
654 2020-08-26 14:05:02   product

In [33]:
web.loc[(web['sku'] == "41") | (web['sku'] == "38") | (web['total_sales'] == 41) | (web['total_sales'] == 38)]
#web.loc[(web['total_sales'] == 41) | (web['sku'] == "41")]

sku  total_sales  post_author           post_date       post_date_gmt  \
92   16264           38            2 2019-05-03 11:18:00 2019-05-03 09:18:00   
536     38           38            2 2018-04-18 12:25:58 2018-04-18 10:25:58   
568  16580           41            2 2019-07-24 09:31:48 2019-07-24 07:31:48   
664     41            0            2 2018-04-14 12:01:43 2018-04-14 10:01:43   

                                            post_title       post_modified  \
92      Château de La Liquière Faugères L'Ampoule 2019 2020-08-24 18:15:03   
536         Emile Boeckel Crémant Brut Blanc de Blancs 2020-08-27 17:15:03   
568           Domaine Giudicelli Patrimonio Blanc 2019 2020-08-27 10:12:58   
664  Marcel Windholtz Eau de Vie de Marc de Gewurzt... 2020-08-03 10:25:02   

      post_modified_gmt post_type  
92  2020-08-24 16:15:03   product  
536 2020-08-27 15:15:03   product  
568 2020-08-27 08:12:58   product  
664 2020-08-03 08:25:02   product

In [34]:
# WEB : SKU non numérique
web[~web['sku'].astype(str).str.isnumeric()].sort_values(by='post_date')

sku  total_sales  post_author           post_date  \
101  bon-cadeau-25-euros           10            1 2018-06-01 13:53:46   
241                  NaN           10            2 2018-07-31 12:07:23   
172                  NaN            3            2 2018-08-08 11:23:43   
249              13127-1            0            2 2020-06-09 15:42:04   

          post_date_gmt                                       post_title  \
101 2018-06-01 11:53:46                                Bon cadeau de 25€   
241 2018-07-31 10:07:23       Pierre Jean Villa Côte Rôtie Fongeant 2017   
172 2018-08-08 09:23:43  Pierre Jean Villa Condrieu Jardin Suspendu 2018   
249 2020-06-09 13:42:04     Clos du Mont-Olivet Châteauneuf-du-Pape 2007   

          post_modified   post_modified_gmt post_type  
101 2018-06-01 14:13:57 2018-06-01 12:13:57   product  
241 2019-11-02 13:24:15 2019-11-02 12:24:15   product  
172 2019-11-02 13:24:01 2019-11-02 12:24:01   product  
249 2020-07-20 17:09:06 2020-07-20 15:09:06   product

In [35]:
# ERP : PRODUCT_ID NON ASSOCIE A UN SKU
erp.loc[(erp['product_id'] == 4594) | (erp['product_id'] == 5070) |(erp['product_id'] == 5075)]

product_id  onsale_web  price  stock_quantity stock_status
228        4594           1  144.0               0   outofstock
449        5070           1   84.7               0   outofstock
450        5075           1   43.3               0   outofstock

In [37]:
# LIAISON : SKU NON NUMERIQUE
#etude = liaison[~liaison['sku'].astype(str).str.isnumeric()]
#etude = etude.fillna(0)
#etude.loc[etude['sku'] != 0]

In [38]:
web[web['sku'].astype(str).str.contains('14680')]

sku  total_sales  post_author           post_date       post_date_gmt  \
605  14680            6            2 2018-04-18 22:06:42 2018-04-18 20:06:42   

                                            post_title       post_modified  \
605  Domaine Saint-Nicolas Fiefs Vendéens Blanc Le ... 2020-08-08 17:45:03   

      post_modified_gmt post_type  
605 2020-08-08 15:45:03   product

In [39]:
web.groupby('post_title').filter(lambda x: len(x) > 1)

sku  total_sales  post_author           post_date  \
183    15292            1            2 2018-02-28 13:43:33   
249  13127-1            0            2 2020-06-09 15:42:04   
300    14000            2            2 2018-04-13 13:32:03   
316    14828            0            2 2018-11-26 09:52:56   
462    16034            3            2 2018-09-25 15:35:26   
654    16068            1            2 2020-02-22 14:28:32   

          post_date_gmt                                         post_title  \
183 2018-02-28 12:43:33           Domaine Hauvette IGP Alpilles Jaspe 2017   
249 2020-06-09 13:42:04       Clos du Mont-Olivet Châteauneuf-du-Pape 2007   
300 2018-04-13 11:32:03  Marc Colin Et Fils Chassagne-Montrachet Blanc ...   
316 2018-11-26 08:52:56  Marc Colin Et Fils Chassagne-Montrachet Blanc ...   
462 2018-09-25 13:35:26       Clos du Mont-Olivet Châteauneuf-du-Pape 2007   
654 2020-02-22 13:28:32           Domaine Hauvette IGP Alpilles Jaspe 2017   

          post_modified   post_modified_gmt post_type  
183 2020-08-27 10:24:18 2020-08-27 08:24:18   product  
249 2020-07-20 17:09:06 2020-07-20 15:09:06   product  
300 2019-10-07 09:30:10 2019-10-07 07:30:10   product  
316 2020-03-27 09:30:10 2020-03-27 08:30:10   product  
462 2020-08-21 14:25:03 2020-08-21 12:25:03   product  
654 2020-08-26 16:05:02 2020-08-26 14:05:02   product

In [ ]:
#web[web['sku'].astype(str).str.contains('13127-1')]
#web.loc[web['sku']== '13127-1', 'sku'] = '13128'
#web.loc[web['sku']== '131278']

#web[web['sku'].astype(str).str.contains('bon-cadeau-25-euros')]
#web.loc[web['sku']== 'bon-cadeau-25-euros', 'sku'] = '13129'
#web.loc[web['sku']== '13129']

In [ ]:

#erp_liaison[erp_liaison['sku'].astype(str).str.contains('13127-1')]
#erp_liaison.loc[erp_liaison['sku'] == '13127-1', "sku"] = '13128'
#erp_liaison.loc[erp_liaison['sku']== '13128']

#erp_liaison[erp_liaison['sku'].astype(str).str.contains('bon-cadeau-25-euros')]
#erp_liaison.loc[erp_liaison['sku'] == 'bon-cadeau-25-euros', "sku"] = '13129'
#erp_liaison.loc[erp_liaison['sku']== '13129']


In [ ]:
#profileWEB = ProfileReport(web, title="Profiling Report WEB")
#profileWEB

<div style="background-color: RGB(400,150,50);" >
<h2 style="margin: auto; padding: 20px; color:#fff; ">FIN DE ZONE DE TEST </h2>
</div>

<div style="background-color: RGB(0,150,250);" >
<h2 style="margin: auto; padding: 20px; color:#fff; ">Etape 3 - Exploration du fichier Liaison</h2>
</div>

In [40]:
#Renommer la colonne id_web en sku
liaison = liaison.rename(columns={'id_web': 'sku'})

In [41]:

#supprimer les colonnes inutiles (aucune valeurs): Unnamed: 2, Unnamed: 3, Unnamed: 4
drop_col = ['Unnamed: 2', 'Unnamed: 3', 'Unnamed: 4']


liaison.drop(columns=drop_col, inplace=True)


In [42]:

liaison.fillna(0)


product_id      sku
0          3847    15298
1          3849    15296
2          3850    15300
3          4032    19814
4          4039    19815
..          ...      ...
820        7203        0
821        7204        0
822        7247  13127-1
823        7329  14680-1
824        7338    16230

[825 rows x 2 columns]

In [43]:
liaison[~liaison['sku'].astype(str).str.isnumeric()]


product_id      sku
19         4055      NaN
49         4090      NaN
50         4092      NaN
119        4195      NaN
131        4209      NaN
..          ...      ...
819        7201      NaN
820        7203      NaN
821        7204      NaN
822        7247  13127-1
823        7329  14680-1

[94 rows x 2 columns]

In [44]:
etude = liaison[~liaison['sku'].astype(str).str.isnumeric()]
etude = etude.fillna(0)
etude.loc[etude['sku'] != 0]

product_id                  sku
443        4954  bon-cadeau-25-euros
822        7247              13127-1
823        7329              14680-1

In [45]:
liaison.loc[(liaison['sku'] == "41") | (liaison['sku'] == "38")]

product_id sku
277        4634  41
347        4729  38

<div style="background-color: RGB(0,150,250);" >
<h2 style="margin: auto; padding: 20px; color:#fff; ">Etape 4 - Analyse du fichier ERP avec Liaison</h2>
</div>

In [46]:
#1 : Je merge ERP et liaison pour vérifier si les ref_sku manquant sont des produit commercialisé off_line

erp_liaison = pd.merge(erp, liaison, how="left", on='product_id')


In [47]:
#J'affiche les lignes qui ne sont pas au normes
erp_liaison[~erp_liaison['sku'].astype(str).str.isnumeric()]


product_id  onsale_web  price  stock_quantity stock_status  \
228        4594           1  144.0               0   outofstock   
411        4954           1   25.0               0      instock   
449        5070           1   84.7               0   outofstock   
450        5075           1   43.3               0   outofstock   
715        7247           1   54.8              23      instock   

                     sku  
228                  NaN  
411  bon-cadeau-25-euros  
449                  NaN  
450                  NaN  
715              13127-1

In [48]:
erp_liaison.loc[erp_liaison['sku'].astype(str).str.isnumeric()]

product_id  onsale_web  price  stock_quantity stock_status    sku
0          3847           1   24.2               0   outofstock  15298
1          3849           1   34.3               0   outofstock  15296
2          3850           1   20.8               0   outofstock  15300
3          4032           1   14.1               0   outofstock  19814
4          4039           1   46.0               0   outofstock  19815
..          ...         ...    ...             ...          ...    ...
711        6928           1   19.0              20      instock  15741
712        6930           1    8.4              83      instock  16135
713        7023           1   27.5              15      instock  15891
714        7025           1   69.0               2      instock  15887
716        7338           1   16.3              45      instock  16230

[712 rows x 6 columns]

In [ ]:
#erp_liaison.loc[erp_liaison['sku'] == '13127-1', "sku"] = '13128'
#erp_liaison.loc[erp_liaison['sku']== '13128']

<div style="background-color: RGB(0,150,250);" >
<h2 style="margin: auto; padding: 20px; color:#fff; ">Etape 5 - Analyse du fichier WEB avec Liaison</h2>
</div>

In [49]:
web_liaison = pd.merge(web, liaison, how="left", on='sku')
web_liaison.loc[web_liaison['sku'] == "41"]

sku  total_sales  post_author           post_date       post_date_gmt  \
844  41            0            2 2018-04-14 12:01:43 2018-04-14 10:01:43   

                                            post_title       post_modified  \
844  Marcel Windholtz Eau de Vie de Marc de Gewurzt... 2020-08-03 10:25:02   

      post_modified_gmt post_type  product_id  
844 2020-08-03 08:25:02   product        4634

In [53]:
web_liaison.loc[(web_liaison['sku'] == "15292")|(web_liaison['sku'] == "13127-1")|(web_liaison['sku'] == "14000")|(web_liaison['sku'] == "14828")|(web_liaison['sku'] == "16034")|(web_liaison['sku'] == "16068")]
#web.groupby('post_title').filter(lambda x: len(x) > 1)

sku  total_sales  post_author           post_date  \
273    15292            1            2 2018-02-28 13:43:33   
429  13127-1            0            2 2020-06-09 15:42:04   
480    14000            2            2 2018-04-13 13:32:03   
496    14828            0            2 2018-11-26 09:52:56   
642    16034            3            2 2018-09-25 15:35:26   
834    16068            1            2 2020-02-22 14:28:32   

          post_date_gmt                                         post_title  \
273 2018-02-28 12:43:33           Domaine Hauvette IGP Alpilles Jaspe 2017   
429 2020-06-09 13:42:04       Clos du Mont-Olivet Châteauneuf-du-Pape 2007   
480 2018-04-13 11:32:03  Marc Colin Et Fils Chassagne-Montrachet Blanc ...   
496 2018-11-26 08:52:56  Marc Colin Et Fils Chassagne-Montrachet Blanc ...   
642 2018-09-25 13:35:26       Clos du Mont-Olivet Châteauneuf-du-Pape 2007   
834 2020-02-22 13:28:32           Domaine Hauvette IGP Alpilles Jaspe 2017   

          post_modified   post_modified_gmt post_type  product_id  
273 2020-08-27 10:24:18 2020-08-27 08:24:18   product        4288  
429 2020-07-20 17:09:06 2020-07-20 15:09:06   product        7247  
480 2019-10-07 09:30:10 2019-10-07 07:30:10   product        4597  
496 2020-03-27 09:30:10 2020-03-27 08:30:10   product        5544  
642 2020-08-21 14:25:03 2020-08-21 12:25:03   product        5465  
834 2020-08-26 16:05:02 2020-08-26 14:05:02   product        6665

In [51]:
web_liaison[web_liaison['sku'].astype(str).str.contains('14680')]

sku  total_sales  post_author           post_date       post_date_gmt  \
785  14680            6            2 2018-04-18 22:06:42 2018-04-18 20:06:42   

                                            post_title       post_modified  \
785  Domaine Saint-Nicolas Fiefs Vendéens Blanc Le ... 2020-08-08 17:45:03   

      post_modified_gmt post_type  product_id  
785 2020-08-08 15:45:03   product        4757

In [55]:
all = pd.merge(erp_liaison, web, how="outer", on="sku")
all.loc[all['sku'].isna()]

product_id  onsale_web  price  stock_quantity stock_status  sku  \
714        4594           1  144.0               0   outofstock  NaN   
715        4594           1  144.0               0   outofstock  NaN   
716        5070           1   84.7               0   outofstock  NaN   
717        5070           1   84.7               0   outofstock  NaN   
718        5075           1   43.3               0   outofstock  NaN   
719        5075           1   43.3               0   outofstock  NaN   

     total_sales  post_author           post_date       post_date_gmt  \
714            3            2 2018-08-08 11:23:43 2018-08-08 09:23:43   
715           10            2 2018-07-31 12:07:23 2018-07-31 10:07:23   
716            3            2 2018-08-08 11:23:43 2018-08-08 09:23:43   
717           10            2 2018-07-31 12:07:23 2018-07-31 10:07:23   
718            3            2 2018-08-08 11:23:43 2018-08-08 09:23:43   
719           10            2 2018-07-31 12:07:23 2018-07-31 10:07:23   

                                          post_title       post_modified  \
714  Pierre Jean Villa Condrieu Jardin Suspendu 2018 2019-11-02 13:24:01   
715       Pierre Jean Villa Côte Rôtie Fongeant 2017 2019-11-02 13:24:15   
716  Pierre Jean Villa Condrieu Jardin Suspendu 2018 2019-11-02 13:24:01   
717       Pierre Jean Villa Côte Rôtie Fongeant 2017 2019-11-02 13:24:15   
718  Pierre Jean Villa Condrieu Jardin Suspendu 2018 2019-11-02 13:24:01   
719       Pierre Jean Villa Côte Rôtie Fongeant 2017 2019-11-02 13:24:15   

      post_modified_gmt post_type  
714 2019-11-02 12:24:01   product  
715 2019-11-02 12:24:15   product  
716 2019-11-02 12:24:01   product  
717 2019-11-02 12:24:15   product  
718 2019-11-02 12:24:01   product  
719 2019-11-02 12:24:15   product